## Amazon Redshift Provisioned 
## Verify Automatic or Manul WLM configuration

In [0]:
SELECT c.wlm_mode,
       scc.service_class::text AS service_class_id,
       CASE
         WHEN scc.service_class BETWEEN 1 AND 4 THEN 'System'
         WHEN scc.service_class = 5 THEN 'Superuser'
         WHEN scc.service_class BETWEEN 6 AND 13 THEN 'Manual WLM'
         WHEN scc.service_class = 14 THEN 'SQA'
         WHEN scc.service_class = 15 THEN 'Redshift Maintenance'
         WHEN scc.service_class BETWEEN 100 AND 107 THEN 'Auto WLM'
       END AS service_class_category,
       trim(scc.name) AS queue_name,
       CASE
         WHEN scc.num_query_tasks = -1 THEN 'auto'
         ELSE scc.num_query_tasks::text
       END AS slots,
       CASE
         WHEN scc.query_working_mem = -1 THEN 'auto'
         ELSE scc.query_working_mem::text
       END AS query_working_memory_mb_per_slot,
       nvl(cast(ROUND(((scc.num_query_tasks*scc.query_working_mem)::NUMERIC/ mem.total_memory_mb::NUMERIC)*100,0)::NUMERIC(38,4) as varchar(12)),'auto') cluster_memory_pct,
       scc.max_execution_time AS query_timeout,
       trim(scc.concurrency_scaling) AS concurrency_scaling,
       trim(scc.query_priority) AS queue_priority,
       nvl(qc.qmr_rule_count,0) AS qmr_rule_count,
       LISTAGG(DISTINCT TRIM(qmr.qmr_rule),',') within group(ORDER BY rule_name) qmr_rule,
       LISTAGG(TRIM(cnd.condition),', ') condition
FROM stv_wlm_service_class_config scc
  INNER JOIN stv_wlm_classification_config cnd ON scc.service_class = cnd.action_service_class
  CROSS JOIN (SELECT CASE
                       WHEN COUNT(1) > 0 THEN 'auto'
                       ELSE 'manual'
                     END AS wlm_mode
              FROM stv_wlm_service_class_config
              WHERE service_class >= 100) c
  CROSS JOIN (SELECT SUM(num_query_tasks*query_working_mem) AS total_memory_mb
              FROM stv_wlm_service_class_config
              WHERE service_class BETWEEN 6 AND 13) mem
  LEFT OUTER JOIN (SELECT service_class,
                          COUNT(DISTINCT rule_name) AS qmr_rule_count
                   FROM stv_wlm_qmr_config
                   GROUP BY service_class) qc ON (scc.service_class = qc.service_class)
  LEFT OUTER JOIN (SELECT service_class,
                          rule_name,
                          rule_name || ':' || '[' || action || '] ' || metric_name || metric_operator || CAST(metric_value AS VARCHAR(256)) qmr_rule
                   FROM stv_wlm_qmr_config) qmr ON scc.service_class = qmr.service_class
WHERE scc.service_class > 4
GROUP BY 1,
         2,
         3,
         4,
         5,
         6,
         7,
         8,
         9,
         10,
         11
ORDER BY 2 ASC;

## Metrics per WLM queue for the last 7 days

In [0]:
SELECT w.service_class AS wlm_queue,
       DATE_TRUNC('day',w.service_class_start_time) AS start_hour,
       COUNT(w.query) AS queries,
       ROUND(SUM(w.total_exec_time / 1000000::FLOAT),2) AS exec_sec,
       ROUND(SUM(w.total_queue_time / 1000000::FLOAT),2) AS queue_sec,
       SUM(CASE WHEN a.action = 'abort' THEN 1 ELSE 0 END) AS qmr_abort,
       SUM(m.query_temp_blocks_to_disk) AS total_spill_mb,
       SUM(m.scan_row_count) AS total_row_scan,
       SUM(m.join_row_count) AS total_join_rows,
       SUM(m.nested_loop_join_row_count) AS total_nl_join_rows,
       SUM(m.return_row_count) AS total_return_rows
FROM stl_wlm_query AS w
  LEFT JOIN stl_wlm_rule_action AS a USING (userid,service_class,query)
  LEFT JOIN svl_query_metrics_summary AS m USING (userid,service_class,query)
WHERE w.userid > 1
AND   w.service_class_start_time > DATEADD(day,-7,CURRENT_DATE)
GROUP BY 1,
         2
ORDER BY wlm_queue,
         start_hour DESC;

## WLM estimated memory used in percentile

In [0]:
select service_class, count(*), avg(est_peak_mem),
 ROUND(PERCENTILE_CONT (0.25) WITHIN GROUP(ORDER BY est_peak_mem),2) AS p25_s,
 ROUND(PERCENTILE_CONT (0.50) WITHIN GROUP(ORDER BY est_peak_mem),2) AS p50_s,
 ROUND(PERCENTILE_CONT (0.75) WITHIN GROUP(ORDER BY est_peak_mem),2) AS p75_s,
 ROUND(PERCENTILE_CONT (0.90) WITHIN GROUP(ORDER BY est_peak_mem),2) AS p90_s,
 ROUND(PERCENTILE_CONT (0.95) WITHIN GROUP(ORDER BY est_peak_mem),2) AS p95_s,
 ROUND(PERCENTILE_CONT (0.99) WITHIN GROUP(ORDER BY est_peak_mem),2) AS p99_s,
 min(est_peak_mem) as minmem,
 max(est_peak_mem) as maxmem
 from stl_wlm_query
 where service_class > 4
 group by service_class;

## Queue Health

In [0]:
with workload as
(
select trim(sq."database") as dbname
      ,case 
	     when sq.concurrency_scaling_status = 1 then 'burst'	        
			 else 'main' end as concurrency_scaling_status 
      ,case 
       when sl.source_query is not null then 'result_cache'       
			 else rtrim(swsc.name) end as queue_name 
			,swq.service_class 
      ,case
       when swq.service_class between 1 and 4 then 'System'
       when swq.service_class = 5 then 'Superuser'
       when swq.service_class between 6 and 13 then'Manual WLM queues'
       when swq.service_class = 14 then 'SQA'
       when swq.service_class = 15 then 'Redshift Maintenance'
       when swq.service_class between 100 and 107 then 'Auto WLM'
       end as service_class_category 	  
      ,sq.query as query_id
      ,case 
         when regexp_instr(sq.querytxt, '(padb_|pg_internal)'             ) then 'OTHER'
         when regexp_instr(sq.querytxt, '([uU][nN][dD][oO][iI][nN][gG]) ' ) then 'SYSTEM'
         when regexp_instr (sq.querytxt,'([aA][uU][tT][oO][mM][vV])'      ) then 'AUTOMV'
         when regexp_instr(sq.querytxt, '[uU][nN][lL][oO][aA][dD]'        ) then 'UNLOAD'
         when regexp_instr(sq.querytxt, '[cC][uU][rR][sS][oO][rR] '       ) then 'CURSOR'
         when regexp_instr(sq.querytxt, '[fF][eE][tT][cC][hH] '           ) then 'CURSOR'
         WHEN regexp_instr (sq.querytxt,'[cC][rR][eE][aA][tT][eE] '       ) then 'CTAS'
         when regexp_instr(sq.querytxt, '[dD][eE][lL][eE][tT][eE] '       ) then 'DELETE'
         when regexp_instr(sq.querytxt, '[uU][pP][dD][aA][tT][eE] '       ) then 'UPDATE'
         when regexp_instr(sq.querytxt, '[iI][nN][sS][eE][rR][tT] '       ) then 'INSERT'
         when regexp_instr(sq.querytxt, '[vV][aA][cC][uU][uU][mM][ :]'    ) then 'VACUUM'
         when regexp_instr(sq.querytxt, '[aA][nN][aA][lL][yY][zZ][eE] '   ) then 'ANALYZE'		 
         when regexp_instr(sq.querytxt, '[sS][eE][lL][eE][cC][tT] '       ) then 'SELECT'
         when regexp_instr(sq.querytxt, '[cC][oO][pP][yY] '               ) then 'COPY'
         else 'OTHER' 
       end as query_type 
      ,date_trunc('hour',sq.starttime) as workload_exec_hour
      ,nvl(swq.est_peak_mem/1024.0/1024.0/1024.0,0.0) as est_peak_mem_gb
      ,decode(swq.final_state, 'Completed',decode(swr.action, 'abort',0,decode(sq.aborted,0,1,0)),'Evicted',0,null,decode(sq.aborted,0,1,0)::int) as is_completed
      ,decode(swq.final_state, 'Completed',decode(swr.action, 'abort',1,0),'Evicted',1,null,0) as is_evicted_aborted
      ,decode(swq.final_state, 'Completed',decode(swr.action, 'abort',0,decode(sq.aborted,1,1,0)),'Evicted',0,null,decode(sq.aborted,1,1,0)::int) as is_user_aborted
	    ,case when sl.from_sp_call is not null then 1 else 0 end as from_sp_call
	    ,case when alrt.num_events is null then 0 else alrt.num_events end as alerts
	    ,case when dsk.num_diskbased > 0 then 1 else 0 end as is_query_diskbased
	    ,nvl(c.num_compile_segments,0) as num_compile_segments
      ,cast(case when sqms.query_queue_time is null then 0 else sqms.query_queue_time end as decimal(26,6)) as query_queue_time_secs
	    ,nvl(c.max_compile_time_secs,0) as max_compile_time_secs
	    ,sl.starttime
	    ,sl.endtime
	    ,sl.elapsed
      ,cast(sl.elapsed * 0.000001 as decimal(26,6)) as query_execution_time_secs	
      ,sl.elapsed * 0.000001 - nvl(c.max_compile_time_secs,0)  - nvl(sqms.query_queue_time,0) as actual_execution_time_secs	  
      ,case when sqms.query_temp_blocks_to_disk is null then 0 else sqms.query_temp_blocks_to_disk end as query_temp_blocks_to_disk_mb
      ,cast(case when sqms.query_cpu_time is null then 0 else sqms.query_cpu_time end as decimal(26,6)) as query_cpu_time_secs 
	    ,nvl(sqms.scan_row_count,0) as scan_row_count
      ,nvl(sqms.return_row_count,0) as return_row_count
      ,nvl(sqms.nested_loop_join_row_count,0) as nested_loop_join_row_count
      ,nvl(uc.usage_limit_count,0) as cs_usage_limit_count
  from stl_query sq
  inner join svl_qlog sl on (sl.userid = sq.userid and sl.query = sq.query)
  left outer join svl_query_metrics_summary sqms on (sqms.userid = sq.userid and sqms.query = sq.query)					
  left outer join stl_wlm_query swq on (sq.userid = swq.userid and sq.query = swq.query)
  left outer join stl_wlm_rule_action swr on (sq.userid = swr.userid and sq.query = swr.query and swq.service_class = swr.service_class)
  left outer join stv_wlm_service_class_config swsc on (swsc.service_class = swq.service_class)
  left outer join (select sae.query
                         ,cast(1 as integer) as num_events
                     from svcs_alert_event_log sae
                   group by sae.query) as alrt on (alrt.query = sq.query)  
  left outer join (select sqs.userid
                         ,sqs.query
                         ,1 as num_diskbased
                     from svcs_query_summary sqs    
                    where sqs.is_diskbased = 't'
                   group by sqs.userid, sqs.query
                   ) as dsk on (dsk.userid = sq.userid and dsk.query = sq.query)  
  left outer join (select userid, xid,  pid, query
                         ,max(datediff(ms, starttime, endtime)*1.0/1000) as max_compile_time_secs
	                     ,sum(compile) as num_compile_segments
                     from svcs_compile
                   group by userid, xid,  pid, query
                  ) c on (c.userid = sq.userid and c.xid = sq.xid and c.pid = sq.pid and c.query = sq.query)                 
  left outer join (select query,xid,pid
                          ,count(1) as usage_limit_count
                      from stl_usage_control 
                     where feature_type = 'CONCURRENCY_SCALING'
                   group by query, xid, pid) uc on (uc.xid = sq.xid and uc.pid = sq.pid and uc.query = sq.query)                  	   
  where sq.userid <> 1 
    and sq.querytxt not like 'padb_fetch_sample%'
    and sq.starttime >= dateadd(day,-7,current_date)
)
select workload_exec_hour
      ,service_class_category
      ,service_class
      ,queue_name
      ,concurrency_scaling_status
      ,dbname
      ,query_type
      ,sum(is_completed) + sum(is_user_aborted) + sum(is_evicted_aborted) as total_query_count
      ,sum(is_completed) as completed_query_count
      ,sum(is_user_aborted) as user_aborted_count
      ,sum(is_evicted_aborted) as wlm_evicted_count
      ,round(sum(est_peak_mem_gb),4) as total_est_peak_mem_gb
      ,sum(is_query_diskbased) as total_disk_spill_count
      ,sum(num_compile_segments) as total_compile_count
      ,round(sum(query_temp_blocks_to_disk_mb/1024.0),4) as total_disk_spill_gb
      ,sum(alerts) as total_query_alert_count
      ,sum(from_sp_call) as total_called_proc_count
	  ,avg(query_execution_time_secs) as avg_query_execution_time_secs
	  ,max(query_execution_time_secs) as max_query_execution_time_secs
      ,sum(query_execution_time_secs) as total_query_execution_time_secs
	  ,avg(max_compile_time_secs) as avg_compile_time_secs
	  ,max(max_compile_time_secs) as max_compile_time_secs
      ,sum(max_compile_time_secs) as total_compile_time_secs
	  ,avg(query_queue_time_secs) as avg_query_queue_time_secs
	  ,max(query_queue_time_secs) as max_query_queue_time_secs
      ,sum(query_queue_time_secs) as total_query_queue_time_secs
	  ,avg(actual_execution_time_secs) as avg_actual_execution_time_secs
      ,sum(actual_execution_time_secs) as total_actual_execution_time_secs
      ,sum(query_cpu_time_secs) as total_query_cpu_time_secs
      ,sum(cs_usage_limit_count) as total_cs_usage_limit_count
      ,sum(scan_row_count) as total_scan_row_count
      ,sum(return_row_count) as total_return_row_count
      ,sum(nested_loop_join_row_count) as total_nl_join_row_count
  from workload
  group by 1,2,3,4,5,6,7
  order by 1,2,3,4,5,6,7;

## Concurrency Scaling Usage

In [0]:
select date_trunc('hour',end_time) as burst_hour
      ,sum(queries) as query_count
      ,sum(usage_in_seconds) as concurrency_usage_in_seconds  
from svcs_concurrency_scaling_usage
group by burst_hour;